In [13]:
import sys, os
from my_keys import MufexKeys
from multiprocessing import cpu_count
import pandas as pd
import numpy as np
from quantfreedom.helpers.helper_funcs import dl_ex_candles
from quantfreedom.core.backtest import or_backtest
from datetime import datetime
from time import gmtime, strftime
import pickle
from quantfreedom.core.enums import FootprintCandlesTuple

from vol_strat import exchange_settings_tuple, static_os_tuple, long_strat

%load_ext autoreload
%autoreload 2

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


In [ ]:
%run -i long_backtest.py

In [ ]:
pd.read_hdf('backtest_results.h5').sort_values('qf_score', ascending=False).head(15)

In [14]:
with open("Volume_Candles_Tuple_mar_apr.pkl", "rb") as f:
    candles: FootprintCandlesTuple = pickle.load(f)

In [2]:
backtest_results = or_backtest(
    candles=candles,
    exchange_settings_tuple=exchange_settings_tuple,
    static_os_tuple=static_os_tuple,
    strategy=long_strat,
    set_idx=0,
    disable_logger=False,
    plot_results=True,
)

DynamicOrderSettings(
    account_pct_risk_per_trade = 0.03,
    max_trades = 4,
    risk_reward = 5.0,
    sl_based_on_add_pct = 0.002,
    sl_based_on_lookback = 30,
    sl_bcb_type = 6,
    sl_to_be_cb_type = 10,
    sl_to_be_when_pct = 0.0,
    trail_sl_bcb_type = 6,
    trail_sl_by_pct = 0.01,
    trail_sl_when_pct = 0.01,
)
IndicatorSettings(
    cur_candle_rsi_below = 40,
    cur_dur_less_than = 5,
    dur_x_times_faster = 5,
    ema_length = 25,
    max_av_duration = 1,
    min_delta_dif = 2000000,
    rsi_dur_lb = 2,
    rsi_is_below = 30,
    rsi_length = 14,
)


In [4]:
backtest_results['order_status'] == "EntryFilled"

0       True
1       True
2      False
3       True
4      False
       ...  
210    False
211     True
212    False
213     True
214    False
Name: order_status, Length: 215, dtype: bool

In [42]:
backtest_results

set_idx  bar_idx      timestamp    order_status                datetime  \
0          0     2151  1709513273264     EntryFilled 2024-03-04 00:47:53.264   
1          0     2152  1709513274791     EntryFilled 2024-03-04 00:47:54.791   
2          0     2157  1709513345084  StopLossFilled 2024-03-04 00:49:05.084   
3          0     2964  1709561027019     EntryFilled 2024-03-04 14:03:47.019   
4          0     3004  1709562543464        MovedTSL 2024-03-04 14:29:03.464   
..       ...      ...            ...             ...                     ...   
210        0    63949  1713968809002  StopLossFilled 2024-04-24 14:26:49.002   
211        0    63951  1713968812051     EntryFilled 2024-04-24 14:26:52.051   
212        0    63955  1713968825844  StopLossFilled 2024-04-24 14:27:05.844   
213        0    67050  1714363146266     EntryFilled 2024-04-29 03:59:06.266   
214        0    67091  1714368784025  StopLossFilled 2024-04-29 05:33:04.025   

       equity  available_balance  cash_borrowed  cash_used  average_entry  \
0    1000.000            902.295      12339.044     97.705        63400.0   
1    1000.000            740.227      32690.047    259.773        63422.7   
2     942.915            942.915            NaN        NaN            NaN   
3     942.915            875.246       7915.505     67.669        64710.0   
4         NaN                NaN            NaN        NaN            NaN   
..        ...                ...            ...        ...            ...   
210   614.217            614.217            NaN        NaN            NaN   
211   614.217            572.744       4684.354     41.473        65430.0   
212   596.273            596.273            NaN        NaN            NaN   
213   596.273            552.927       5270.080     43.346        62230.0   
214   579.349            579.349            NaN        NaN            NaN   

     ...  entry_size_usd  entry_price  exit_price  position_size_asset  \
0    ...       12436.749      63400.0         NaN                0.196   
1    ...        8174.027      63480.0         NaN                0.325   
2    ...             NaN          NaN     63323.1                  NaN   
3    ...        7983.174      64710.0         NaN                0.123   
4    ...             NaN          NaN         NaN                  NaN   
..   ...             ...          ...         ...                  ...   
210  ...             NaN          NaN     65269.2                  NaN   
211  ...        4725.827      65430.0         NaN                0.072   
212  ...             NaN          NaN     65259.2                  NaN   
213  ...        5313.426      62230.0         NaN                0.085   
214  ...             NaN          NaN     62105.5                  NaN   

     position_size_usd  realized_pnl  sl_pct  sl_price  tp_pct  tp_price  
0            12436.749           NaN   0.100   63323.1     1.3   64222.0  
1            20610.776           NaN   0.200   63323.1     1.5   64403.2  
2                  NaN       -57.085     NaN       NaN     NaN       NaN  
3             7983.174           NaN   0.200   64560.6     1.8   65903.4  
4                  NaN           NaN   0.001   64746.0     NaN       NaN  
..                 ...           ...     ...       ...     ...       ...  
210                NaN       -17.986     NaN       NaN     NaN       NaN  
211           4725.827           NaN   0.300   65259.2     2.0   66735.3  
212                NaN       -17.944     NaN       NaN     NaN       NaN  
213           5313.426           NaN   0.200   62105.5     1.7   63281.8  
214                NaN       -16.924     NaN       NaN     NaN       NaN  

[215 rows x 26 columns]

In [41]:
backtest_results['order_status'].unique()

array(['EntryFilled', 'StopLossFilled', 'MovedTSL', 'TakeProfitFilled'],
      dtype=object)

In [38]:
entries = np.ones((candles.candle_asset_volumes.size, 5), dtype=object)
entries[:, 1:] = None
tps = np.ones((candles.candle_asset_volumes.size, 5), dtype=object)
tps[:, 1:] = None
sls = np.ones((candles.candle_asset_volumes.size, 5), dtype=object)
sls[:, 1:] = None

In [44]:
entry_prices = backtest_results[["bar_idx", "entry_price", "sl_price", "tp_price"]][
    backtest_results["order_status"] == "EntryFilled"
].to_numpy()
entry_prices

array([[ 2151. , 63400. , 63323.1, 64222. ],
       [ 2152. , 63480. , 63323.1, 64403.2],
       [ 2964. , 64710. , 64560.6, 65903.4],
       [ 4461. , 66800. , 66636.5, 68078.3],
       [ 4494. , 65430. , 65129.5, 67383.7],
       [ 5352. , 68540. , 68412.9, 69648.4],
       [ 5359. , 67740. , 67604.5, 68884.8],
       [ 5363. , 67490. , 67335.1, 68730.1],
       [ 5548. , 67020. , 66846. , 68352.3],
       [ 5813. , 64850. , 64720.3, 65945.9],
       [ 5815. , 64670. , 64720.3, 64864.9],
       [ 6454. , 63450. , 63343.1, 64422.3],
       [ 6597. , 62160. , 61886. , 63958.6],
       [ 8437. , 64960. , 64710.3, 66656.5],
       [ 9776. , 67000. , 66786.2, 68531.1],
       [11082. , 67170. , 66866. , 69153.2],
       [11167. , 66290. , 66197.3, 67210.9],
       [11168. , 66270. , 66197.3, 67150.9],
       [14665. , 71500. , 71337. , 72808.3],
       [15216. , 72350. , 72255.2, 73323.2],
       [15354. , 71200. , 71107.5, 72153.8],
       [15361. , 70900. , 70758.2, 72098.1],
       [15

In [45]:
entries[entry_prices[:, 0].astype(np.int_), 1] = entry_prices[:, 1]
sls[entry_prices[:, 0].astype(np.int_), 1] = entry_prices[:, 2]
tps[entry_prices[:, 0].astype(np.int_), 1] = entry_prices[:, 3]

In [52]:
entries_list = entries.tolist()
tps_list = tps.tolist()
sls_list = sls.tolist()

In [ ]:
from requests import get
get("https://api.ipify.org")